In [1]:
import requests
from bs4 import BeautifulSoup as BS
import pandas as pd
import time
import matplotlib.pyplot as plt
import numpy as np
from sportsreference.nba.roster import Player
from sportsreference.ncaab.roster import Roster
import time
import re
import ast
pd.set_option('display.max_columns', 100)
pd.options.display.max_rows = 4000

In [2]:
Draft_years= []
for i in range(1985,2001):
    Draft_years.append(str(i))

Getting NBA Info:

In [3]:
def get_draft_class_career_stats(year):
    page = requests.get('https://www.basketball-reference.com/draft/NBA_'+str(year)+'.html')
    #print('here')
    soup = BS(page.content, 'html.parser')
    table_body=soup.find('tbody')
    rows = table_body.find_all('tr')
    data=[]
    hrefs=[]
    for row in rows:
        cols=row.find_all('td')
        cols=[x.text.strip() for x in cols]
        data.append(cols)
    column_names=['Pick','Team','Name','College','Yrs','G','MP','PTS','TRB','AST','FG%','3P%','FT%', 'MP', 'PTS', 'TRB','AST','WS','WS/48','BPM','VORP']
    df = pd.DataFrame(data, columns= column_names)
    df['Year']= year
    time.sleep(.3)
    return df

In [4]:
def get_hrefs(year):
    page = requests.get('https://www.basketball-reference.com/draft/NBA_'+str(year)+'.html')
    #print('here')
    soup = BS(page.content, 'html.parser')
    table_body=soup.find('tbody')
    rows = table_body.find_all('tr')
    hrefs=[]
    for row in rows:
        try:
            href=row.find_all('a')
            x= (href[2])
            x= re.findall('\"+(/players/+.*)\"', str(x))
            if len(x)>0:
                hrefs.append(x)
            else:
                pass
            continue
        except:
            pass
    return hrefs

In [5]:
def get_player_info(href1):
    page = requests.get('https://www.basketball-reference.com'+str(href1))
    #Name of Player
    soup = BS(page.content, 'html.parser')
    table_body=soup.find_all(itemprop= "name")
    table_body
    name= re.findall('<h1 itemprop=\"name\">(.*)</h1>', str(table_body))
    if len(name)==0:
        name= re.findall('<span>(.*)</span>', str(table_body))
    else:
        pass
    #Bio
    soup = BS(page.content, 'html.parser')
    table_body=soup.find_all('p')
    work=table_body[0:10]
    #print(work)
    height= re.findall('(\d*cm)', str(work))
    weight= re.findall('(\d*kg)', str(work))
    bday= re.findall('data-birth=\"(\d*\-\d*\-\d*)', str(work))
    position= re.findall('(Center|Power Forward|Small Forward|Shooting Guard|Point Guard)', str(work))
    #accolades
    accolades_body=soup.find(id="bling")
    All_Star_apps= re.findall('(\d*)x All Star', str(accolades_body))
    All_NBA_apps= re.findall('(\d*)x All-NBA', str(accolades_body))
    All_Def_apps= re.findall('(\d*)x All-Defensive', str(accolades_body))
    HOF= re.findall('(Hall of Fame)', str(accolades_body))
    empty_list=0
    if len(All_Star_apps)==empty_list:
        All_Star_apps='0'
    else:
        All_Star_apps=All_Star_apps[0]
    if len(All_NBA_apps)==empty_list:
        All_NBA_apps='0'
    else:
        All_NBA_apps=All_NBA_apps[0]
    if len(All_Def_apps)==empty_list:
        All_Def_apps='0'
    else:
        All_Def_apps= All_Def_apps[0]
    if len(HOF)==empty_list:
        HOF='0'
    else:
        HOF= HOF[0]
    if len(position)==1:
        bio= [name[0],height[0],weight[0],bday[0],position[0],position[0],position[0],All_Star_apps,All_NBA_apps,All_Def_apps,HOF]
    else:
        pass
    if len(position)==2:
        bio= [name[0],height[0],weight[0],bday[0],position[0],position[1],position[0],All_Star_apps,All_NBA_apps,All_Def_apps,HOF]
    else:
        pass
    if len(position)==3:
        bio= [name[0],height[0],weight[0],bday[0],position[0],position[1],position[2],All_Star_apps,All_NBA_apps,All_Def_apps,HOF]
    else:
        pass
    if len(position)==4:
        bio= [name[0],height[0],weight[0],bday[0],position[0],position[1],position[2],position[3],All_Star_apps,All_NBA_apps,All_Def_apps,HOF]
    else:
        pass
    if len(position)==5:
        bio= [name[0],height[0],weight[0],bday[0],position[1],position[2],position[3],position[4],All_Star_apps,All_NBA_apps,All_Def_apps,HOF]
    else:
        pass
    return bio

In [6]:
def put_it_all_together(year):
    hrefs= get_hrefs(year)
    players= []
    for href in range(len(hrefs)):
        player= get_player_info(hrefs[href][0])
        players.append(player)
        time.sleep(.3)
    return players

In [7]:
info= []
draft_classes= []
df=get_draft_class_career_stats(1985)
for year in Draft_years:
    draft_class= get_draft_class_career_stats(year)
    df=pd.concat([df,draft_class])
    df.drop_duplicates(subset ='Name', keep = 'first', inplace = True)

In [8]:
df_info= put_it_all_together(1985)
df_info = pd.DataFrame(put_it_all_together(1985), columns=['Name','Height','Weight','Birthday','Position1','Position2','Position3','All_Star_apps','All_NBA_apps','All_Def_apps','HOF'])
for year in Draft_years:
    info1= pd.DataFrame(put_it_all_together(year), columns=['Name','Height','Weight','Birthday','Position1','Position2','Position3','All_Star_apps','All_NBA_apps','All_Def_apps','HOF'])
    df_info=pd.concat([df_info,info1])
    df_info.drop_duplicates(subset ='Name', keep = 'first', inplace = True)

In [9]:
df_info

Name Height Weight    Birthday       Position1  \
0           Patrick Ewing  213cm  108kg  1962-08-05          Center   
1          Wayman Tisdale  206cm  108kg  1964-06-09   Power Forward   
2         Benoit Benjamin  213cm  113kg  1964-11-22          Center   
3         Xavier McDaniel  201cm   92kg  1963-06-04   Power Forward   
4              Jon Koncak  213cm  113kg  1963-05-17          Center   
5              Joe Kleine  211cm  115kg  1962-01-04          Center   
6            Chris Mullin  198cm   90kg  1963-07-30   Small Forward   
7         Detlef Schrempf  208cm  106kg  1963-01-21   Power Forward   
8          Charles Oakley  203cm  102kg  1963-12-18          Center   
9             Ed Pinckney  206cm   88kg  1963-03-27   Power Forward   
10              Keith Lee  208cm   97kg  1962-12-28   Power Forward   
11            Kenny Green  198cm   95kg  1964-10-11   Small Forward   
12            Karl Malone  206cm  113kg  1963-07-24   Power Forward   
13      Alfredrick Hughes  196cm   97kg  1962-07-19  Shooting Guard   
14        Blair Rasmussen  213cm  113kg  1962-11-13          Center   
15        Bill Wennington  213cm  111kg  1963-04-26          Center   
16               Uwe Blab  216cm  114kg  1962-03-26          Center   
17             Joe Dumars  190cm   86kg  1963-05-24     Point Guard   
18           Steve Harris  196cm   88kg  1963-10-15  Shooting Guard   
19            Sam Vincent  188cm   83kg  1963-05-18     Point Guard   
20         Terry Catledge  203cm   99kg  1963-08-22   Power Forward   
21         Jerry Reynolds  203cm   90kg  1962-12-23   Small Forward   
22             A.C. Green  206cm   99kg  1963-10-04   Power Forward   
23           Terry Porter  190cm   88kg  1963-04-08     Point Guard   
24             Mike Smrek  213cm  113kg  1962-08-31          Center   
25            Bill Martin  201cm   92kg  1962-08-16   Small Forward   
26         Dwayne McClain  198cm   83kg  1963-02-07   Small Forward   
27            Ken Johnson  203cm  108kg  1962-11-07   Power Forward   
28          Mike Brittain  213cm  106kg  1963-06-21          Center   
29             Manute Bol  231cm   90kg  1962-10-16          Center   
30             Nick Vanos  216cm  115kg  1963-04-13          Center   
31            Greg Stokes  208cm   99kg  1963-08-05   Power Forward   
32          Tyrone Corbin  198cm   95kg  1962-12-31   Small Forward   
33            Yvon Joseph  211cm  111kg  1957-10-31          Center   
34           Carey Scurry  201cm   85kg  1962-12-04   Small Forward   
35        Fernando Martín  206cm   99kg  1962-03-25          Center   
36             Mark Acres  211cm   99kg  1962-11-15          Center   
37        Lorenzo Charles  201cm  102kg  1963-11-25   Small Forward   
38          Barry Stevens  196cm   88kg  1963-01-17   Small Forward   
39          Voise Winters  203cm   90kg  1962-10-12   Small Forward   
40       Hot Rod Williams  211cm   97kg  1962-08-09          Center   
41          Adrian Branch  201cm   83kg  1963-11-17   Small Forward   
42         Gerald Wilkins  198cm   83kg  1963-09-11   Small Forward   
43            Brad Wright  211cm  102kg  1962-03-26   Power Forward   
44           Sam Mitchell  198cm   95kg  1963-09-02   Power Forward   
45           Sedric Toney  188cm   80kg  1962-04-13     Point Guard   
46            Perry Young  196cm   95kg  1963-08-04  Shooting Guard   
47         Harold Keeling  193cm   83kg  1963-09-18  Shooting Guard   
48          Michael Adams  178cm   73kg  1963-01-19     Point Guard   
49             Mike Brown  206cm  116kg  1963-07-19          Center   
50           Fred Cofield  190cm   86kg  1962-01-04     Point Guard   
51          Alex Stivrins  203cm   99kg  1962-11-29   Power Forward   
52        Arvydas Sabonis  221cm  126kg  1964-12-19          Center   
53             Mark Davis  198cm   88kg  1963-06-08   Small Forward   
54             Scott Roth  203cm   96kg  1963-06-03   Small Forward   
55           Delaney Rudd  188cm   81kg  1962

In [10]:
df_complete= pd.merge(df,df_info,how='left',on='Name')

In [11]:
df_complete['College']= np.where(df_complete.College=="", 'None', df_complete.College)
df_complete

Pick  Team                     Name  \
0        1   NYK            Patrick Ewing   
1        2   IND           Wayman Tisdale   
2        3   LAC          Benoit Benjamin   
3        4   SEA          Xavier McDaniel   
4        5   ATL               Jon Koncak   
5        6   SAC               Joe Kleine   
6        7   GSW             Chris Mullin   
7        8   DAL          Detlef Schrempf   
8        9   CLE           Charles Oakley   
9       10   PHO              Ed Pinckney   
10      11   CHI                Keith Lee   
11      12   WSB              Kenny Green   
12      13   UTA              Karl Malone   
13      14   SAS        Alfredrick Hughes   
14      15   DEN          Blair Rasmussen   
15      16   DAL          Bill Wennington   
16      17   DAL                 Uwe Blab   
17      18   DET               Joe Dumars   
18      19   HOU             Steve Harris   
19      20   BOS              Sam Vincent   
20      21   PHI           Terry Catledge   
21      22   MIL           Jerry Reynolds   
22      23   LAL               A.C. Green   
23      24   POR             Terry Porter   
24    None  None                     None   
25      25   POR               Mike Smrek   
26      26   IND              Bill Martin   
27      27   IND           Dwayne McClain   
28      28   CHI              Ken Johnson   
29      29   SAS            Mike Brittain   
30      30   CLE            Calvin Duncan   
31      31   WSB               Manute Bol   
32      32   PHO               Nick Vanos   
33      33   PHI              Greg Stokes   
34      34   CHI           Aubrey Sherrod   
35      35   SAS            Tyrone Corbin   
36      36   NJN              Yvon Joseph   
37      37   UTA             Carey Scurry   
38      38   NJN          Fernando Martín   
39      39   POR        George Montgomery   
40      40   DAL               Mark Acres   
41      41   ATL          Lorenzo Charles   
42      42   GSW           Bobby Lee Hurt   
43      43   DEN            Barry Stevens   
44      44   PHI            Voise Winters   
45      45   CLE         Hot Rod Williams   
46      46   CHI            Adrian Branch   
47      47   NYK           Gerald Wilkins   
48      48   IND          Kenny Patterson   
49      49   GSW              Brad Wright   
50      50   DAL            Leonard Allen   
51      51   SAC          Charles Bradley   
52      52   LAC         Anicet Lavodrama   
53      53   SEA             Rolando Lamb   
54      54   HOU             Sam Mitchell   
55      55   CLE             Herb Johnson   
56      56   PHO            Jerry Everett   
57      57   HOU            Michael Payne   
58      58   WSB             Vernon Moore   
59      59   ATL             Sedric Toney   
60      60   DET              Andre Goode   
61      61   POR              Perry Young   
62      62   NJN             Nigel Manuel   
63      63   DAL           Harold Keeling   
64      64   DET           Richie Johnson   
65      65   WSB                Ken Perry   
66      66   SAC            Michael Adams   
67      67   PHI              Steve Black   
68      68   MIL          Eugene McDowell   
69      69   CHI               Mike Brown   
70      70   BOS             Andre Battle   
71      71   GSW           Luster Goodwin   
72      72   IND           Vince Hamilton   
73      73   NYK             Fred Cofield   
74      74   LAC               Jim Deines   
75      75   SEA            Alex Stivrins   
76      76   SAC           Willie Simmons   
77      77   ATL          Arvydas Sabonis   
78      78   PHO             Granger Hall   
79      79   CLE               Mark Davis   
80      80   CHI              Craig Beard   
81      81   WSB             Richie Adams   
82      82   SAS               Scott Roth   
83      83   UTA             Delaney Rudd   
84      84   ATL              John Battle   
85      85   POR             Joe Atkinson   
86      86   DAL           Bubba Jennings   
87      87   DET                Spud Webb   
8

In [12]:
just_ncaa_players= df_complete[df_complete['College']!= 'None']

In [13]:
just_ncaa_players

Pick  Team                   Name  \
0        1   NYK          Patrick Ewing   
1        2   IND         Wayman Tisdale   
2        3   LAC        Benoit Benjamin   
3        4   SEA        Xavier McDaniel   
4        5   ATL             Jon Koncak   
5        6   SAC             Joe Kleine   
6        7   GSW           Chris Mullin   
7        8   DAL        Detlef Schrempf   
8        9   CLE         Charles Oakley   
9       10   PHO            Ed Pinckney   
10      11   CHI              Keith Lee   
11      12   WSB            Kenny Green   
12      13   UTA            Karl Malone   
13      14   SAS      Alfredrick Hughes   
14      15   DEN        Blair Rasmussen   
15      16   DAL        Bill Wennington   
16      17   DAL               Uwe Blab   
17      18   DET             Joe Dumars   
18      19   HOU           Steve Harris   
19      20   BOS            Sam Vincent   
20      21   PHI         Terry Catledge   
21      22   MIL         Jerry Reynolds   
22      23   LAL             A.C. Green   
23      24   POR           Terry Porter   
24    None  None                   None   
25      25   POR             Mike Smrek   
26      26   IND            Bill Martin   
27      27   IND         Dwayne McClain   
28      28   CHI            Ken Johnson   
29      29   SAS          Mike Brittain   
30      30   CLE          Calvin Duncan   
31      31   WSB             Manute Bol   
32      32   PHO             Nick Vanos   
33      33   PHI            Greg Stokes   
34      34   CHI         Aubrey Sherrod   
35      35   SAS          Tyrone Corbin   
36      36   NJN            Yvon Joseph   
37      37   UTA           Carey Scurry   
39      39   POR      George Montgomery   
40      40   DAL             Mark Acres   
41      41   ATL        Lorenzo Charles   
42      42   GSW         Bobby Lee Hurt   
43      43   DEN          Barry Stevens   
44      44   PHI          Voise Winters   
45      45   CLE       Hot Rod Williams   
46      46   CHI          Adrian Branch   
47      47   NYK         Gerald Wilkins   
48      48   IND        Kenny Patterson   
49      49   GSW            Brad Wright   
50      50   DAL          Leonard Allen   
51      51   SAC        Charles Bradley   
52      52   LAC       Anicet Lavodrama   
53      53   SEA           Rolando Lamb   
54      54   HOU           Sam Mitchell   
55      55   CLE           Herb Johnson   
56      56   PHO          Jerry Everett   
57      57   HOU          Michael Payne   
58      58   WSB           Vernon Moore   
59      59   ATL           Sedric Toney   
60      60   DET            Andre Goode   
61      61   POR            Perry Young   
62      62   NJN           Nigel Manuel   
63      63   DAL         Harold Keeling   
64      64   DET         Richie Johnson   
65      65   WSB              Ken Perry   
66      66   SAC          Michael Adams   
67      67   PHI            Steve Black   
68      68   MIL        Eugene McDowell   
69      69   CHI             Mike Brown   
70      70   BOS           Andre Battle   
71      71   GSW         Luster Goodwin   
72      72   IND         Vince Hamilton   
73      73   NYK           Fred Cofield   
74      74   LAC             Jim Deines   
75      75   SEA          Alex Stivrins   
76      76   SAC         Willie Simmons   
78      78   PHO           Granger Hall   
79      79   CLE             Mark Davis   
80      80   CHI            Craig Beard   
81      81   WSB           Richie Adams   
82      82   SAS             Scott Roth   
83      83   UTA           Delaney Rudd   
84      84   ATL            John Battle   
85      85   POR           Joe Atkinson   
86      86   DAL         Bubba Jennings   
87      87   DET              Spud Webb   
88      88   HOU            Mike Brooks   
89      89   DEN          Pete Williams   
90      90   PHI         Derrick Gervin   
91      91   MIL         Cozell McQueen   
92      92   LAL          Dexter Shouse   
93      93   BOS            Cliff Weber   
94     

In [14]:
df_complete

Pick  Team                     Name  \
0        1   NYK            Patrick Ewing   
1        2   IND           Wayman Tisdale   
2        3   LAC          Benoit Benjamin   
3        4   SEA          Xavier McDaniel   
4        5   ATL               Jon Koncak   
5        6   SAC               Joe Kleine   
6        7   GSW             Chris Mullin   
7        8   DAL          Detlef Schrempf   
8        9   CLE           Charles Oakley   
9       10   PHO              Ed Pinckney   
10      11   CHI                Keith Lee   
11      12   WSB              Kenny Green   
12      13   UTA              Karl Malone   
13      14   SAS        Alfredrick Hughes   
14      15   DEN          Blair Rasmussen   
15      16   DAL          Bill Wennington   
16      17   DAL                 Uwe Blab   
17      18   DET               Joe Dumars   
18      19   HOU             Steve Harris   
19      20   BOS              Sam Vincent   
20      21   PHI           Terry Catledge   
21      22   MIL           Jerry Reynolds   
22      23   LAL               A.C. Green   
23      24   POR             Terry Porter   
24    None  None                     None   
25      25   POR               Mike Smrek   
26      26   IND              Bill Martin   
27      27   IND           Dwayne McClain   
28      28   CHI              Ken Johnson   
29      29   SAS            Mike Brittain   
30      30   CLE            Calvin Duncan   
31      31   WSB               Manute Bol   
32      32   PHO               Nick Vanos   
33      33   PHI              Greg Stokes   
34      34   CHI           Aubrey Sherrod   
35      35   SAS            Tyrone Corbin   
36      36   NJN              Yvon Joseph   
37      37   UTA             Carey Scurry   
38      38   NJN          Fernando Martín   
39      39   POR        George Montgomery   
40      40   DAL               Mark Acres   
41      41   ATL          Lorenzo Charles   
42      42   GSW           Bobby Lee Hurt   
43      43   DEN            Barry Stevens   
44      44   PHI            Voise Winters   
45      45   CLE         Hot Rod Williams   
46      46   CHI            Adrian Branch   
47      47   NYK           Gerald Wilkins   
48      48   IND          Kenny Patterson   
49      49   GSW              Brad Wright   
50      50   DAL            Leonard Allen   
51      51   SAC          Charles Bradley   
52      52   LAC         Anicet Lavodrama   
53      53   SEA             Rolando Lamb   
54      54   HOU             Sam Mitchell   
55      55   CLE             Herb Johnson   
56      56   PHO            Jerry Everett   
57      57   HOU            Michael Payne   
58      58   WSB             Vernon Moore   
59      59   ATL             Sedric Toney   
60      60   DET              Andre Goode   
61      61   POR              Perry Young   
62      62   NJN             Nigel Manuel   
63      63   DAL           Harold Keeling   
64      64   DET           Richie Johnson   
65      65   WSB                Ken Perry   
66      66   SAC            Michael Adams   
67      67   PHI              Steve Black   
68      68   MIL          Eugene McDowell   
69      69   CHI               Mike Brown   
70      70   BOS             Andre Battle   
71      71   GSW           Luster Goodwin   
72      72   IND           Vince Hamilton   
73      73   NYK             Fred Cofield   
74      74   LAC               Jim Deines   
75      75   SEA            Alex Stivrins   
76      76   SAC           Willie Simmons   
77      77   ATL          Arvydas Sabonis   
78      78   PHO             Granger Hall   
79      79   CLE               Mark Davis   
80      80   CHI              Craig Beard   
81      81   WSB             Richie Adams   
82      82   SAS               Scott Roth   
83      83   UTA             Delaney Rudd   
84      84   ATL              John Battle   
85      85   POR             Joe Atkinson   
86      86   DAL           Bubba Jennings   
87      87   DET                Spud Webb   
8

In [15]:
#df_complete.to_csv('1985_2000_draft_class_NBA.csv')

Get NCAA data:

In [60]:
def get_NCAA_href(href1):
    page = requests.get('https://www.basketball-reference.com'+str(href1))
    soup = BS(page.content, 'html.parser')
    link= re.findall('(https:\/\/www\.sports-reference\.com\/cbb\/players\/.*\.html)', str(soup))
    if len(link)>0:
        link= link[0]
        return link
    else:
        return

In [61]:
hrefs2000= get_hrefs(2000)
website=[]
for href in hrefs2000:
    #time.sleep(.3)
    if website==0:
        a= get_NCAA_href(href[0])
        website.append(a)
    else:
        a= get_NCAA_href(href[0])
        website.append(a)
website

['https://www.sports-reference.com/cbb/players/kenyon-martin-1.html',
 'https://www.sports-reference.com/cbb/players/stromile-swift-1.html',
 None,
 'https://www.sports-reference.com/cbb/players/marcus-fizer-1.html',
 'https://www.sports-reference.com/cbb/players/mike-miller-1.html',
 'https://www.sports-reference.com/cbb/players/dermarr-johnson-1.html',
 'https://www.sports-reference.com/cbb/players/chris-mihm-1.html',
 'https://www.sports-reference.com/cbb/players/jamal-crawford-1.html',
 'https://www.sports-reference.com/cbb/players/joel-przybilla-1.html',
 'https://www.sports-reference.com/cbb/players/keyon-dooling-1.html',
 'https://www.sports-reference.com/cbb/players/jerome-moiso-1.html',
 'https://www.sports-reference.com/cbb/players/etan-thomas-1.html',
 'https://www.sports-reference.com/cbb/players/courtney-alexander-1.html',
 'https://www.sports-reference.com/cbb/players/mateen-cleaves-1.html',
 'https://www.sports-reference.com/cbb/players/jason-collier-1.html',
 None,
 'ht

In [67]:
column_names=['School', 'Conf', 'G', 'GS', 'MP', 'FG', 'FGA', 'FG%', '2P', '2PA', '2P%', '3P', '3PA', '3P%', 'FT', 'FTA', 'FT%', 'ORB', 'DRB', 'TRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS', 'SOS']
len(column_names)

27

In [94]:
def get_player_NCAA_stats(website):
    #Pull Final Year NCAA Stats
    if website== None:
        return
    page = requests.get(website)
    soup = BS(page.content, 'html.parser')
    table_body=soup.find('tbody')
    rows = table_body.find_all('tr')
    data=[]
    hrefs=[]
    for row in rows:
        cols=row.find_all('td')
        cols=[x.text.strip() for x in cols]
        data.append(cols)
    column_names=['School', 'Conf', 'G', 'GS', 'MP', 'FG', 'FGA', 'FG%', '2P', '2PA', '2P%', '3P', '3PA', '3P%', 'FT', 'FTA', 'FT%', 'ORB', 'DRB', 'TRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS','Blank', 'SOS']
    df = pd.DataFrame(data, columns= column_names)
    df['Yrs_College']= len(df)
    df= df.tail(1)
    df.reset_index(inplace= True, drop= True)
    time.sleep(.3)
    
    #Get Name
    table_body=soup.find_all(itemprop= "name")
    table_body
    name= re.findall('<h1 itemprop=\"name\">(.*)</h1>', str(table_body))
    if len(name)==0:
        name= re.findall('<span>(.*)</span>', str(table_body))
    else:
        pass
    df['Name']= name
    columns=['Name','Yrs_College','School', 'Conf', 'G', 'GS', 'MP', 'FG', 'FGA', 'FG%', '2P', '2PA', '2P%', '3P', '3PA', '3P%', 'FT', 'FTA', 'FT%', 'ORB', 'DRB', 'TRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS','Blank', 'SOS']
    df= df[columns]
    df.drop(columns=['Blank', 'GS', 'ORB', 'DRB'], inplace=True)
    
    return df